# <span style="background-color:#005e81; padding:5px; border-radius:5px;">**Arquivo.pt**</span>

In [ ]:
import pandas as pd
from datetime import datetime
import requests
from requests.adapters import HTTPAdapter, Retry
import re
from urllib.parse import urlsplit
from unidecode import unidecode 
from bs4 import BeautifulSoup
from urllib.parse import urljoin, unquote
from urllib3.util.retry import Retry
from concurrent.futures import ThreadPoolExecutor, as_completed
import spacy
from rapidfuzz import process, fuzz

## <span style="background-color:#005e81; padding:5px; border-radius:5px;">**1. Extração notícias do Arquivo.pt**</span>

### <span style="background-color:#005e81; padding:5px; border-radius:5px;">**1.1. Extração de notícias usando a API do Arquivo.pt**</span>

Vamos usar **3 queries** em sequência: 
- "cartel concursos públicos"
- "irregularidades concursos públicos"
- "conluio concursos públicos"

Guarda tudo no dataset `links` e elimina duplicados entre queries.

In [ ]:
# NÃO CORRER ESTA CÉLULA OUTRA VEZ

BASE_URL = "https://arquivo.pt/textsearch"

def build_session(total_retries=5, backoff=0.5, timeout=20):
    s = requests.Session()
    retries = Retry(total=total_retries, backoff_factor=backoff,
                    status_forcelist=[429,500,502,503,504], allowed_methods=["GET"])
    adapter = HTTPAdapter(max_retries=retries, pool_connections=10, pool_maxsize=10)
    s.mount("http://", adapter); s.mount("https://", adapter)
    orig = s.request
    def _req(*args, **kw): kw.setdefault("timeout", timeout); return orig(*args, **kw)
    s.request = _req
    return s

def yyyymmdd(d: datetime) -> str: return d.strftime("%Y%m%d")

def month_segments(start: datetime, end: datetime):
    cur = datetime(start.year, start.month, 1)
    end_first = datetime(end.year, end.month, 1)
    while cur <= end_first:
        seg_end = (pd.Timestamp(cur) + pd.offsets.MonthEnd(0)).to_pydatetime()
        yield max(cur, start), min(seg_end, end)
        cur = (pd.Timestamp(cur) + pd.offsets.MonthBegin(1)).to_pydatetime()

def fetch_links_segment(session, query, seg_start, seg_end, verbose=True):
    offset, links = 0, []
    while True:
        params = {
            "q": query,
            "from": yyyymmdd(seg_start),
            "to": yyyymmdd(seg_end),
            "maxItems": 100,
            "offset": offset,
        }
        r = session.get(BASE_URL, params=params)
        if r.status_code != 200: break
        items = r.json().get("response_items", []) or []
        if not items: break
        batch = [(it.get("linkToArchive") or it.get("linkToFile") or "") for it in items]
        links.extend([lk for lk in batch if lk])
        if verbose: print(f"{seg_start:%Y-%m} offset={offset} (+{len(items)})")
        offset += len(items)
        if len(items) < 100: break
    return links

def get_links_arquivo_monthly_for_query(session, query, start_date, end_date, verbose=True):
    """Extrai links únicos (por query) segmentando por mês."""
    start = datetime.fromisoformat(start_date)
    end = datetime.fromisoformat(end_date)
    seen, all_links = set(), []
    for seg_s, seg_e in month_segments(start, end):
        ls = fetch_links_segment(session, query, seg_s, seg_e, verbose=verbose)
        new = [lk for lk in ls if lk not in seen]
        for lk in new: seen.add(lk)
        if verbose:
            print(f"✅ {seg_s:%Y-%m} [{query}] → {len(new)} novos (acum: {len(seen)})")
        all_links.extend(new)
    return all_links

def get_links_for_queries(queries, start_date="2000-01-01", end_date="2025-09-01", verbose=True) -> pd.DataFrame:
    """Corre várias queries, junta e deduplica globalmente."""
    session = build_session()
    global_seen, rows = set(), []
    for q in queries:
        if verbose: print(f"\n🔎 Query: {q}")
        links_q = get_links_arquivo_monthly_for_query(session, q, start_date, end_date, verbose=verbose)
        added = 0
        for lk in links_q:
            if lk not in global_seen:
                global_seen.add(lk)
                rows.append(lk)
                added += 1
        if verbose: print(f"➡️  '{q}': +{added} links únicos (acum: {len(global_seen)})")
    df = pd.DataFrame({"link": rows})
    return df

if __name__ == "__main__":
    QUERIES = [
        "cartel concursos públicos",
        "irregularidades concursos públicos",
        "conluio concursos públicos",
    ]
    links = get_links_for_queries(QUERIES, start_date="2000-01-01", end_date="2025-09-01", verbose=True)
    print(f"\nTotal de links únicos (todas as queries): {len(links)}")
    links.to_csv("links_arquivo_multiquery.csv", index=False)

In [2]:
links = pd.read_csv("links_arquivo_multiquery.csv")
links

link
0      https://arquivo.pt/wayback/20001121030500/http...
1      https://arquivo.pt/wayback/20001206073100/http...
2      https://arquivo.pt/wayback/20001215054500/http...
3      https://arquivo.pt/wayback/20010107153600/http...
4      https://arquivo.pt/wayback/20010119100900/http...
...                                                  ...
29308  https://arquivo.pt/wayback/20201003204347/http...
29309  https://arquivo.pt/wayback/20201003183755/http...
29310  https://arquivo.pt/wayback/20201003170802/http...
29311  https://arquivo.pt/wayback/20201003171715/http...
29312  https://arquivo.pt/wayback/20210101021831/http...

[29313 rows x 1 columns]

In [3]:
# verificação: os links são únicos
links["link"].duplicated().sum()  

0

In [4]:
links['link'][27436]

'https://arquivo.pt/wayback/20180914172129/https://observador.pt/2018/09/14/concorrencia-acusa-5-empresas-de-cartel-nos-concursos-para-a-rede-ferroviaria-mota-engil-e-teixeira-duarte-sao-visadas/'

- Existem casos em que duas notícias estão duplicadas mas têm data/hora diferentes. A data/hora estão incluídas no link, o que torna links diferentes apesar de ser a mesma notícia. Por isso, vamos deduplicar por URL original e manter a captura mais recente.

In [5]:
def _canon_url(u: str) -> str:
    """
    Chave canónica simples: host em minúsculas (sem 'www.'), path sem '/' final.
    Ignora query/fragment.
    """
    s = urlsplit(str(u))
    host = s.netloc.lower()
    if host.startswith("www."):
        host = host[4:]
    path = s.path.rstrip("/")
    return f"{host}{path}"

def dedupe_por_url_original_mais_recente(
    df: pd.DataFrame,
    cols: dict | None = None
) -> tuple[pd.DataFrame, pd.DataFrame]:
    """
    Dedupe por página original (retira /wayback/<timestamp>/...), mantendo a captura mais recente.
    """
    c_link = (cols or {}).get("link", "link")

    report_rows = []
    cur = df.copy()
    n0 = len(cur)
    report_rows.append({"passo": "0_inicial", "antes": n0, "depois": n0, "removidas": 0})

    if c_link not in cur.columns:
        report_rows.append({"passo": "dedupe_url", "antes": n0, "depois": n0, "removidas": 0})
        return cur, pd.DataFrame(report_rows)

    # extrair URL original (retira prefixo do Arquivo.pt)
    cur["_orig_url"] = cur[c_link].astype(str).str.replace(
        r"^https?://(?:www\.)?arquivo\.pt/wayback/\d{14}[a-z_]*?/", "",
        regex=True
    )

    # chave canónica (host/path)
    cur["_orig_key"] = cur["_orig_url"].map(_canon_url)

    # timestamp da captura (para ordenar por mais recente)
    cur["_captured_at"] = pd.to_datetime(
        cur[c_link].astype(str).str.extract(r"/wayback/(\d{14})", expand=False),
        format="%Y%m%d%H%M%S",
        errors="coerce"
    )

    # ordenar por mais recente e deduplicar por chave canónica
    cur_dedup = (cur.sort_values("_captured_at", ascending=False)
                   .drop_duplicates(subset="_orig_key", keep="first")
                   .reset_index(drop=True)
                 )

    cur_dedup = cur_dedup.drop(columns=["_orig_url", "_orig_key"])

    n1 = len(cur_dedup)
    report_rows.append({"passo": "dedupe_url", "antes": n0, "depois": n1, "removidas": n0 - n1})
    report = pd.DataFrame(report_rows)
    return cur_dedup, report

In [6]:
links, rep = dedupe_por_url_original_mais_recente(links)
rep

passo  antes  depois  removidas
0   0_inicial  29313   29313          0
1  dedupe_url  29313   14281      15032

> Neste passo de filtragem foram **removidas 15032 links** de notícias.

In [7]:
links

link        _captured_at
0      https://arquivo.pt/wayback/20210101045956/http... 2021-01-01 04:59:56
1      https://arquivo.pt/wayback/20210101035654/http... 2021-01-01 03:56:54
2      https://arquivo.pt/wayback/20210101035650/http... 2021-01-01 03:56:50
3      https://arquivo.pt/wayback/20210101021831/http... 2021-01-01 02:18:31
4      https://arquivo.pt/wayback/20210101005045/http... 2021-01-01 00:50:45
...                                                  ...                 ...
14276  https://arquivo.pt/wayback/20000621040642/http... 2000-06-21 04:06:42
14277  https://arquivo.pt/wayback/20000612210541/http... 2000-06-12 21:05:41
14278  https://arquivo.pt/wayback/20000521120910/http... 2000-05-21 12:09:10
14279  https://arquivo.pt/wayback/20000521120904/http... 2000-05-21 12:09:04
14280  https://arquivo.pt/wayback/20000517095356/http... 2000-05-17 09:53:56

[14281 rows x 2 columns]

### <span style="background-color:#005e81; padding:5px; border-radius:5px;">**1.2. Divisão entre jornais principais, instituições públicas e blogs**</span>

In [8]:
# Adiciona a coluna 'jornal' ao DataFrame `links` (coluna existente: 'link' com URLs do arquivo.pt/wayback)

WB_RX = re.compile(r"/wayback/\d{14}[a-z_]*?/(https?://.+)$", re.I)

def original_url_from_wayback(wb_url: str) -> str | None:
    m = WB_RX.search(str(wb_url))
    return m.group(1) if m else None

def canonical_domain(url: str) -> str | None:
    if not url:
        return None
    d = urlsplit(url).netloc.lower()
    for pref in ("www.", "m.", "mobile.", "amp."):
        if d.startswith(pref):
            d = d[len(pref):]
    return d

STOP_PT = {"aeiou", "xl"}  # hubs a ignorar na cauda do .pt

def brand_key_from_domain(domain: str) -> str | None:
    """
    - *.sapo.pt  -> última label antes de 'sapo.pt'  (ex.: noticias.jn.sapo.pt -> 'jn')
    - *.gov.pt  -> última label antes de 'gov.pt'
    - *.com.pt  -> última label antes de 'com.pt'
    - *.pt       -> última label antes de '.pt'; se for 'aeiou' ou 'xl', usa a anterior
                    (ex.: aeiou.expresso.pt -> 'expresso'; cmjornal.xl.pt -> 'cmjornal')
    - outros TLD -> segunda label (antes do TLD)       (ex.: noticiasaominuto.com -> 'noticiasaominuto')
    """
    if not domain:
        return None
    d = domain.lower()

    if d.endswith(".sapo.pt"):
        core = d[:-len(".sapo.pt")]
        labels = core.split(".")
        return labels[-1] if labels else None
    
    if d.endswith(".com.pt"):
        core = d[:-len(".com.pt")]
        labels = core.split(".")
        return labels[-1] if labels else None
    
    if d.endswith(".gov.pt"):
        core = d[:-len(".gov.pt")]
        labels = core.split(".")
        return labels[-1] if labels else None

    if d.endswith(".pt"):
        core = d[:-len(".pt")]
        labels = core.split(".")
        if not labels:
            return None
        for lab in reversed(labels):
            if lab and lab not in STOP_PT:
                return lab
        return labels[-1]  # fallback

    parts = d.split(".")
    return parts[-2] if len(parts) >= 2 else parts[0]

BRAND_BY_KEY = {
    # Jornais Populares Nacionais
    "publico": "Público",                                   
    "dn": "Diário de Notícias",                            
    "jn": "Jornal de Notícias",                             
    "expresso": "Expresso",                               
    "cmjornal": "Correio da Manhã",                        
    "observador": "Observador",                           
    "visao": "Visão",                                     
    "sabado": "Sábado",                                     
    "rtp": "RTP",
    "jornaleconomico": "Jornal Económico",
    "ionline": "Jornal i",
    "sol": "SOL",
    "destak": "Jornal Destak",
    "tsf": "TSF",
    "jornaldenegocios": "Jornal de Negócios",
    "economico": "Diário Económico",
    "eco": "ECO",
    "zap": "ZAP",
    
    # Instituições públicas
    "autoridadedaconcorrencia": "Autoridade da Concorrência",
    "concorrencia": "Autoridade da Concorrência",
    "tcontas": "Tribunal de Contas",
    "dre": "Diário da República",
    "pgr": "Procuradoria-Geral da República",
    "parlamento": "Assembleia da República",
    "assembleiadarepublica": "Assembleia da República",
    "min-financas": "Ministério das Finanças",
    "cne": "Comissão Nacional de Eleições",
    "eeagrants": "EEA Grants Portugal",
    "portugal": "Governo de Portugal",
    "dgo": "Direção-Geral de Orçamento",
    "min-economia": "Ministério da Economia",
    "governo": "Governo de Portugal",
    "pcm": "Presidência do Conselho de Ministros",
    "mj": "Ministério da Justiça",
    "provedor-jus": "Provedoria de Justiça"
}


# aplicar
links["orig_url"]  = links["link"].map(original_url_from_wayback)
links["dominio"]   = links["orig_url"].map(canonical_domain)
links["brand_key"] = links["dominio"].map(brand_key_from_domain)
links["jornal"]    = links["brand_key"].map(BRAND_BY_KEY).fillna(links["dominio"])

links

link        _captured_at  \
0      https://arquivo.pt/wayback/20210101045956/http... 2021-01-01 04:59:56   
1      https://arquivo.pt/wayback/20210101035654/http... 2021-01-01 03:56:54   
2      https://arquivo.pt/wayback/20210101035650/http... 2021-01-01 03:56:50   
3      https://arquivo.pt/wayback/20210101021831/http... 2021-01-01 02:18:31   
4      https://arquivo.pt/wayback/20210101005045/http... 2021-01-01 00:50:45   
...                                                  ...                 ...   
14276  https://arquivo.pt/wayback/20000621040642/http... 2000-06-21 04:06:42   
14277  https://arquivo.pt/wayback/20000612210541/http... 2000-06-12 21:05:41   
14278  https://arquivo.pt/wayback/20000521120910/http... 2000-05-21 12:09:10   
14279  https://arquivo.pt/wayback/20000521120904/http... 2000-05-21 12:09:04   
14280  https://arquivo.pt/wayback/20000517095356/http... 2000-05-17 09:53:56   

                                                orig_url  \
0      http://www.radiofundacao.net/noticias_geral.ph...   
1      https://www.tsf.pt/portugal/politica/amp/esper...   
2      https://www.tsf.pt/portugal/politica/espero-te...   
3      https://app.parlamento.pt:80/webutils/docs/doc...   
4      https://g1.globo.com/pi/piaui/noticia/2020/12/...   
...                                                  ...   
14276  http://www.cidadevirtual.pt/csmagistratura/bol...   
14277            http://jnoticias.pt/textos/out20519.htm   
14278  http://www.accaosocialista.net/99/1013_01_04_1...   
14279  http://www.accaosocialista.net/99/1009_04_03_1...   
14280              http://jnoticias.pt/textos/text33.htm   

                    dominio        brand_key                   jornal  
0         radiofundacao.net    radiofundacao        radiofundacao.net  
1                    tsf.pt              tsf                      TSF  
2                    tsf.pt              tsf                      TSF  
3      app.parlamento.pt:80       parlamento  Assembleia da República  
4              g1.globo.com            globo             g1.globo.com  
...                     ...              ...                      ...  
14276      cidadevirtual.pt    cidadevirtual         cidadevirtual.pt  
14277          jnoticias.pt        jnoticias             jnoticias.pt  
14278   accaosocialista.net  accaosocialista      accaosocialista.net  
14279   accaosocialista.net  accaosocialista      accaosocialista.net  
14280          jnoticias.pt        jnoticias             jnoticias.pt  

[14281 rows x 6 columns]

Vamos filtrar este dataset com base em **3 critérios**:
- considerar apenas domínios que terminam em .pt
- excluir os blogs: blogspot,weblog,wordpress (guardar num dataset separado)
- excluir jornais com menos de 15 notícias

In [9]:
# ponto de partida
n0 = len(links)
print(f"Passo 0 — total inicial: {n0:,}")

# 1) manter apenas domínios .pt
mask_tld = links["dominio"].str.endswith(".pt", na=False)
n1 = mask_tld.sum()
print(f"Passo 1 — .pt: depois={n1:,} | removidas={n0-n1:,}")

# 2) excluir blogs: blogspot / weblog / wordpress
mask_no_blogs = ~links["dominio"].str.contains(r"(blogs|blogspot|weblog|wordpress)",
                                               case=False, na=False)
n2 = mask_no_blogs.sum()
print(f"Passo 2 — sem blogs: depois={n2:,} | removidas={n0-n2:,}")

# 3) aplicar 1) E 2) em conjunto
mask_both = mask_tld & mask_no_blogs
n3 = mask_both.sum()
print(f"Passo 3 — .pt & sem blogs: depois={n3:,} | removidas={n0-n3:,}")

# 4) manter só jornais com >= 15 notícias (contado após passo 3)
links_p3 = links[mask_both]
counts = links_p3["jornal"].value_counts()
valid = counts[counts >= 15].index

mask_journals = links_p3["jornal"].isin(valid)
n4 = mask_journals.sum()                 # linhas que passam o passo 4
print(f"Passo 4 — jornais com ≥15 notícias: depois={n4:,} | removidas neste passo={n3-n4:,} | removidas desde o início={n0-n4:,}")

# Aplicar os filtros e obter o dataframe final:
links_filtrado = links_p3[mask_journals].reset_index(drop=True)
print(f"Resultado final: {len(links_filtrado):,} linhas | jornais únicos: {links_filtrado['jornal'].nunique():,}")

Passo 0 — total inicial: 14,281
Passo 1 — .pt: depois=8,346 | removidas=5,935
Passo 2 — sem blogs: depois=8,701 | removidas=5,580
Passo 3 — .pt & sem blogs: depois=4,803 | removidas=9,478
Passo 4 — jornais com ≥15 notícias: depois=2,214 | removidas neste passo=2,589 | removidas desde o início=12,067
Resultado final: 2,214 linhas | jornais únicos: 52


C:\Users\beatr\AppData\Local\Temp\ipykernel_24584\2140058589.py:11: UserWarning: This pattern is interpreted as a regular expression, and has match groups. To actually get the groups, use str.extract.
  mask_no_blogs = ~links["dominio"].str.contains(r"(blogs|blogspot|weblog|wordpress)",


In [10]:
links_filtrado = links_filtrado[['link','_captured_at','jornal']]
links_filtrado

link        _captured_at  \
0     https://arquivo.pt/wayback/20210101035654/http... 2021-01-01 03:56:54   
1     https://arquivo.pt/wayback/20210101035650/http... 2021-01-01 03:56:50   
2     https://arquivo.pt/wayback/20210101000938/http... 2021-01-01 00:09:38   
3     https://arquivo.pt/wayback/20201229223108/http... 2020-12-29 22:31:08   
4     https://arquivo.pt/wayback/20201229222247/http... 2020-12-29 22:22:47   
...                                                 ...                 ...   
2209  https://arquivo.pt/wayback/20001209084700/http... 2000-12-09 08:47:00   
2210  https://arquivo.pt/wayback/20001117142800/http... 2000-11-17 14:28:00   
2211  https://arquivo.pt/wayback/20001116204400/http... 2000-11-16 20:44:00   
2212  https://arquivo.pt/wayback/20001102211113/http... 2000-11-02 21:11:13   
2213  https://arquivo.pt/wayback/20000708065437/http... 2000-07-08 06:54:37   

                   jornal  
0                     TSF  
1                     TSF  
2              Observador  
3     Diário da República  
4     Diário da República  
...                   ...  
2209             Expresso  
2210        terravista.pt  
2211        terravista.pt  
2212              Público  
2213        terravista.pt  

[2214 rows x 3 columns]

#### <span style="background-color:#005e81; padding:5px; border-radius:5px;">**1.2.1. Blogs**</span>

> Criar dataset **blogs_pt** só com blogs portugueses excluídos:

In [11]:
# 1) máscara para domínios .pt
mask_pt = links["dominio"].str.endswith(".pt", na=False)

# 2) máscara de blogs
mask_blog = links["dominio"].str.contains(r"(blogs|blogspot|weblog|wordpress)",
                                          case=False, na=False)

# 3) só blogs portugueses (.pt)
mask_blog_pt = mask_pt & mask_blog

blogs_pt = links.loc[mask_blog_pt].copy()
blogs_pt["motivo_exclusao"] = "blog_pt"

print(f"Blogs PT (linhas): {len(blogs_pt):,}")
print(f"Blogs PT (domínios únicos): {blogs_pt['dominio'].nunique():,}")
print("\nTop 10 domínios de blogs PT:")
print(blogs_pt["dominio"].value_counts().head(10))

Blogs PT (linhas): 3,543
Blogs PT (domínios únicos): 736

Top 10 domínios de blogs PT:
dominio
arseteducatio.blogspot.pt            790
ercioafonso.blogspot.pt              195
madespesapublica.blogspot.pt         152
correntes.blogs.sapo.pt              140
candidoneto.blogspot.pt               84
geografiaegeopolitica.blogspot.pt     61
catia-pipoca.blogspot.pt              51
escolapublica2.blogspot.pt            50
007bondeblog.blogspot.pt              41
fmmagazine.blogspot.pt                41
Name: count, dtype: int64


C:\Users\beatr\AppData\Local\Temp\ipykernel_24584\106041616.py:5: UserWarning: This pattern is interpreted as a regular expression, and has match groups. To actually get the groups, use str.extract.
  mask_blog = links["dominio"].str.contains(r"(blogs|blogspot|weblog|wordpress)",


In [12]:
blogs_pt = blogs_pt[['link','_captured_at','jornal']]
blogs_pt

link        _captured_at  \
212    https://arquivo.pt/wayback/20201004220644/http... 2020-10-04 22:06:44   
306    https://arquivo.pt/wayback/20201003180356/http... 2020-10-03 18:03:56   
357    https://arquivo.pt/wayback/20201003153649/http... 2020-10-03 15:36:49   
803    https://arquivo.pt/wayback/20200704115452/http... 2020-07-04 11:54:52   
806    https://arquivo.pt/wayback/20200704082256/http... 2020-07-04 08:22:56   
...                                                  ...                 ...   
13535  https://arquivo.pt/wayback/20041015140855/http... 2004-10-15 14:08:55   
13539  https://arquivo.pt/wayback/20041012024242/http... 2004-10-12 02:42:42   
13552  https://arquivo.pt/wayback/20040925185240/http... 2004-09-25 18:52:40   
13556  https://arquivo.pt/wayback/20040923151413/http... 2004-09-23 15:14:13   
13830  https://arquivo.pt/wayback/20031203022100/http... 2003-12-03 02:21:00   

                                 jornal  
212            daplanicie.blogs.sapo.pt  
306              irritado.blogs.sapo.pt  
357         amar-abrantes.blogs.sapo.pt  
803           porabrantes.blogs.sapo.pt  
806    noticiasdoribatejo.blogs.sapo.pt  
...                                 ...  
13535          ogintonico.weblog.com.pt  
13539           abrelatas.blogs.sapo.pt  
13552         deusvisivel.blogs.sapo.pt  
13556           maisevora.blogs.sapo.pt  
13830             profact.weblog.com.pt  

[3543 rows x 3 columns]

#### <span style="background-color:#005e81; padding:5px; border-radius:5px;">**1.2.2. Jornais Nacionais Populares**</span>

In [13]:
# garantir que não há NaN no nome
links_filtrado["jornal"] = links_filtrado["jornal"].fillna("Desconhecido")

total = len(links_filtrado)

dist = (
    links_filtrado["jornal"]
      .value_counts(dropna=False)
      .rename_axis("jornal")
      .reset_index(name="n")
      .assign(pct=lambda d: (d["n"] / total * 100).round(2))
      .sort_values("pct", ascending=False)
      .reset_index(drop=True))

dist

jornal    n   pct
0                                Público  192  8.67
1                    Diário da República  141  6.37
2                             Observador  125  5.65
3                     Diário de Notícias   97  4.38
4                     Tribunal de Contas   89  4.02
5             Autoridade da Concorrência   82  3.70
6                               Jornal i   78  3.52
7                                    RTP   66  2.98
8                          Jornal Destak   63  2.85
9                               Expresso   62  2.80
10                      Jornal Económico   61  2.76
11               Ministério das Finanças   59  2.66
12                   EEA Grants Portugal   59  2.66
13                   Governo de Portugal   51  2.30
14                                   SOL   49  2.21
15                            sns.gov.pt   48  2.17
16               Assembleia da República   47  2.12
17                      Correio da Manhã   46  2.08
18                      Diário Económico   42  1.90
19                    jornaldoalgarve.pt   41  1.85
20                Ministério da Economia   36  1.63
21                         terravista.pt   35  1.58
22                    Jornal de Notícias   35  1.58
23                 Ministério da Justiça   35  1.58
24                          oribatejo.pt   32  1.45
25                                   TSF   32  1.45
26                    Jornal de Negócios   30  1.36
27         Comissão Nacional de Eleições   29  1.31
28                                 Visão   29  1.31
29                               dgsi.pt   25  1.13
30                         diramb.gov.pt   23  1.04
31                                pcp.pt   23  1.04
32                                qca.pt   22  0.99
33                     jornaldeleiria.pt   21  0.95
34                    ordemdosmedicos.pt   20  0.90
35                                oje.pt   20  0.90
36            Direção-Geral de Orçamento   19  0.86
37                                psd.pt   19  0.86
38                          dnoticias.pt   19  0.86
39                                Sábado   19  0.86
40                         sg.mai.gov.pt   18  0.81
41                       dinheirovivo.pt   18  0.81
42                            rr.sapo.pt   17  0.77
43                                dpp.pt   17  0.77
44                            24.sapo.pt   16  0.72
45       Procuradoria-Geral da República   16  0.72
46                        pwp.netcabo.pt   16  0.72
47                                   ZAP   15  0.68
48                                   ECO   15  0.68
49  Presidência do Conselho de Ministros   15  0.68
50                 Provedoria de Justiça   15  0.68
51                          cm-lisboa.pt   15  0.68

In [14]:
# vamos usar so este conjunto de jornais 
KEEP = {
    "Público",            
    "Diário de Notícias", 
    "Jornal de Notícias", 
    "Expresso",           
    "Correio da Manhã",   
    "Observador",         
    "Visão",              
    "Sábado",             
    "RTP",                
    "Jornal Económico",   
    "Jornal i",           
    "SOL",                
    "Jornal Destak",      
    "TSF",                
    "Jornal de Negócios", 
    "ECO",                
    "ZAP"                 
}

# filter your existing distribution `dist`
popular_journals = dist[dist["jornal"].isin(KEEP)].reset_index(drop=True)
popular_journals

# totais
tot_n   = popular_journals["n"].sum()
tot_pct = popular_journals["pct"].sum().round(2)   # pct relativo à base original

print(f"TOTAL n = {tot_n} | TOTAL pct (base original) = {tot_pct}%")

# acrescentar linha TOTAL ao dataframe
total_row = pd.DataFrame([{"jornal": "TOTAL", "n": tot_n, "pct": tot_pct}])
dist_with_total = pd.concat([popular_journals, total_row], ignore_index=True)
dist_with_total

TOTAL n = 1014 | TOTAL pct (base original) = 45.82%


jornal     n    pct
0              Público   192   8.67
1           Observador   125   5.65
2   Diário de Notícias    97   4.38
3             Jornal i    78   3.52
4                  RTP    66   2.98
5        Jornal Destak    63   2.85
6             Expresso    62   2.80
7     Jornal Económico    61   2.76
8                  SOL    49   2.21
9     Correio da Manhã    46   2.08
10  Jornal de Notícias    35   1.58
11                 TSF    32   1.45
12  Jornal de Negócios    30   1.36
13               Visão    29   1.31
14              Sábado    19   0.86
15                 ZAP    15   0.68
16                 ECO    15   0.68
17               TOTAL  1014  45.82

Agora vamos filtrar o dataset `links` para incluir notícias apenas deste conjunto de jornais nacionais populares:

In [15]:
# conjunto de jornais a manter (como já definiste)
KEEP = {
    "Público", "Diário de Notícias", "Jornal de Notícias", "Expresso",
    "Correio da Manhã", "Observador", "Visão", "Sábado", "RTP",
    "Jornal Económico", "Jornal i", "SOL", "Jornal Destak", "TSF",
    "Jornal de Negócios", "ECO", "ZAP"}

# filtrar o dataframe original
links_popular_journals = (
    links_filtrado
      .assign(jornal=lambda d: d["jornal"].astype("string").str.strip())
      .loc[lambda d: d["jornal"].isin(KEEP)]
      .reset_index(drop=True)
)

links_popular_journals = links_popular_journals[["link",'_captured_at', "jornal"]] # só queremos manter estas 2 colunas
links_popular_journals

link        _captured_at  \
0     https://arquivo.pt/wayback/20210101035654/http... 2021-01-01 03:56:54   
1     https://arquivo.pt/wayback/20210101035650/http... 2021-01-01 03:56:50   
2     https://arquivo.pt/wayback/20210101000938/http... 2021-01-01 00:09:38   
3     https://arquivo.pt/wayback/20201228224031/http... 2020-12-28 22:40:31   
4     https://arquivo.pt/wayback/20201226192545/http... 2020-12-26 19:25:45   
...                                                 ...                 ...   
1009  https://arquivo.pt/wayback/20010118063900/http... 2001-01-18 06:39:00   
1010  https://arquivo.pt/wayback/20010115113300/http... 2001-01-15 11:33:00   
1011  https://arquivo.pt/wayback/20001215054500/http... 2000-12-15 05:45:00   
1012  https://arquivo.pt/wayback/20001209084700/http... 2000-12-09 08:47:00   
1013  https://arquivo.pt/wayback/20001102211113/http... 2000-11-02 21:11:13   

                  jornal  
0                    TSF  
1                    TSF  
2             Observador  
3     Diário de Notícias  
4       Jornal Económico  
...                  ...  
1009             Público  
1010            Expresso  
1011            Expresso  
1012            Expresso  
1013             Público  

[1014 rows x 3 columns]

#### <span style="background-color:#005e81; padding:5px; border-radius:5px;">**1.2.3. Instituições Públicas**</span>

In [16]:
# Sites Governamentais
KEEP = {
    "Autoridade da Concorrência",                  
    "Tribunal de Contas",                          
    "Diário da República",                         
    "Procuradoria-Geral da República",             
    "Assembleia da República",                      
    "Ministério das Finanças",                      
    "Comissão Nacional de Eleições",                
    "EEA Grants Portugal",                          
    "Governo de Portugal",                          
    "Direção-Geral de Orçamento",                   
    "Ministério da Economia",                       
    "Presidência do Conselho de Ministros",         
    "Ministério da Justiça",                        
    "Provedoria de Justiça"                         
}

# filter your existing distribution `dist`
public_intitutions = dist[dist["jornal"].isin(KEEP)].reset_index(drop=True)
public_intitutions

# totais
tot_n   = public_intitutions["n"].sum()
tot_pct = public_intitutions["pct"].sum().round(2)   # pct relativo à base original

print(f"TOTAL n = {tot_n} | TOTAL pct (base original) = {tot_pct}%")

# acrescentar linha TOTAL ao dataframe
total_row = pd.DataFrame([{"jornal": "TOTAL", "n": tot_n, "pct": tot_pct}])
dist_with_total = pd.concat([public_intitutions, total_row], ignore_index=True)
dist_with_total

TOTAL n = 693 | TOTAL pct (base original) = 31.29%


jornal    n    pct
0                    Diário da República  141   6.37
1                     Tribunal de Contas   89   4.02
2             Autoridade da Concorrência   82   3.70
3                Ministério das Finanças   59   2.66
4                    EEA Grants Portugal   59   2.66
5                    Governo de Portugal   51   2.30
6                Assembleia da República   47   2.12
7                 Ministério da Economia   36   1.63
8                  Ministério da Justiça   35   1.58
9          Comissão Nacional de Eleições   29   1.31
10            Direção-Geral de Orçamento   19   0.86
11       Procuradoria-Geral da República   16   0.72
12  Presidência do Conselho de Ministros   15   0.68
13                 Provedoria de Justiça   15   0.68
14                                 TOTAL  693  31.29

In [17]:
KEEP = { 
    "Autoridade da Concorrência", "Tribunal de Contas", "Diário da República", "Procuradoria-Geral da República", "Assembleia da República", 
    "Ministério das Finanças", "Comissão Nacional de Eleições", "EEA Grants Portugal", "Governo de Portugal", "Direção-Geral de Orçamento", "Ministério da Economia", 
    "Presidência do Conselho de Ministros", "Ministério da Justiça", "Provedoria de Justiça"   
}

# filtrar o dataframe original
links_public_intitutions = (
    links_filtrado
      .assign(jornal=lambda d: d["jornal"].astype("string").str.strip())
      .loc[lambda d: d["jornal"].isin(KEEP)]
      .reset_index(drop=True)
)

links_public_intitutions = links_public_intitutions[["link",'_captured_at', "jornal"]] # só queremos manter estas 2 colunas
links_public_intitutions

link        _captured_at  \
0    https://arquivo.pt/wayback/20201229223108/http... 2020-12-29 22:31:08   
1    https://arquivo.pt/wayback/20201229222247/http... 2020-12-29 22:22:47   
2    https://arquivo.pt/wayback/20201213183734/http... 2020-12-13 18:37:34   
3    https://arquivo.pt/wayback/20201211224234/http... 2020-12-11 22:42:34   
4    https://arquivo.pt/wayback/20201209000853/http... 2020-12-09 00:08:53   
..                                                 ...                 ...   
688  https://arquivo.pt/wayback/20010216072402/http... 2001-02-16 07:24:02   
689  https://arquivo.pt/wayback/20010212054243/http... 2001-02-12 05:42:43   
690  https://arquivo.pt/wayback/20010107221300/http... 2001-01-07 22:13:00   
691  https://arquivo.pt/wayback/20001217112200/http... 2000-12-17 11:22:00   
692  https://arquivo.pt/wayback/20001210025200/http... 2000-12-10 02:52:00   

                         jornal  
0           Diário da República  
1           Diário da República  
2           Governo de Portugal  
3    Autoridade da Concorrência  
4            Tribunal de Contas  
..                          ...  
688     Assembleia da República  
689     Assembleia da República  
690     Assembleia da República  
691     Assembleia da República  
692     Assembleia da República  

[693 rows x 3 columns]

Neste momento temos 3 datasets: 
- `blogs_pt`
- `links_popular_journals`
- `links_public_intitutions`

Daqui para a frente vamos concentrar esta pesquisa apenas nos jornais populares (`links_popular_journals`).

In [18]:
links_popular_journals

link        _captured_at  \
0     https://arquivo.pt/wayback/20210101035654/http... 2021-01-01 03:56:54   
1     https://arquivo.pt/wayback/20210101035650/http... 2021-01-01 03:56:50   
2     https://arquivo.pt/wayback/20210101000938/http... 2021-01-01 00:09:38   
3     https://arquivo.pt/wayback/20201228224031/http... 2020-12-28 22:40:31   
4     https://arquivo.pt/wayback/20201226192545/http... 2020-12-26 19:25:45   
...                                                 ...                 ...   
1009  https://arquivo.pt/wayback/20010118063900/http... 2001-01-18 06:39:00   
1010  https://arquivo.pt/wayback/20010115113300/http... 2001-01-15 11:33:00   
1011  https://arquivo.pt/wayback/20001215054500/http... 2000-12-15 05:45:00   
1012  https://arquivo.pt/wayback/20001209084700/http... 2000-12-09 08:47:00   
1013  https://arquivo.pt/wayback/20001102211113/http... 2000-11-02 21:11:13   

                  jornal  
0                    TSF  
1                    TSF  
2             Observador  
3     Diário de Notícias  
4       Jornal Económico  
...                  ...  
1009             Público  
1010            Expresso  
1011            Expresso  
1012            Expresso  
1013             Público  

[1014 rows x 3 columns]

Vamos filtrar este dataset para incluir notícias apenas a partir de 12/05/2010, para coincidir com as datas do nosso dataset de concursos públicos:

In [19]:
# Garantir que a coluna _captured_at está em datetime
links_popular_journals["_captured_at"] = pd.to_datetime(
    links_popular_journals["_captured_at"],
    errors="coerce")

# Filtrar notícias a partir de 12/05/2010 (inclusive)
links_popular_journals = links_popular_journals[
    links_popular_journals["_captured_at"] >= "2010-05-12"
].copy()

In [20]:
links_popular_journals

link        _captured_at  \
0    https://arquivo.pt/wayback/20210101035654/http... 2021-01-01 03:56:54   
1    https://arquivo.pt/wayback/20210101035650/http... 2021-01-01 03:56:50   
2    https://arquivo.pt/wayback/20210101000938/http... 2021-01-01 00:09:38   
3    https://arquivo.pt/wayback/20201228224031/http... 2020-12-28 22:40:31   
4    https://arquivo.pt/wayback/20201226192545/http... 2020-12-26 19:25:45   
..                                                 ...                 ...   
836  https://arquivo.pt/wayback/20100624063145/http... 2010-06-24 06:31:45   
837  https://arquivo.pt/wayback/20100612030446/http... 2010-06-12 03:04:46   
838  https://arquivo.pt/wayback/20100606164020/http... 2010-06-06 16:40:20   
839  https://arquivo.pt/wayback/20100606163914/http... 2010-06-06 16:39:14   
840  https://arquivo.pt/wayback/20100602145911/http... 2010-06-02 14:59:11   

                 jornal  
0                   TSF  
1                   TSF  
2            Observador  
3    Diário de Notícias  
4      Jornal Económico  
..                  ...  
836             Público  
837                 SOL  
838  Jornal de Negócios  
839  Jornal de Negócios  
840            Expresso  

[841 rows x 3 columns]

## <span style="background-color:#005e81; padding:5px; border-radius:5px;">**2. Identificação das entidades adjudicatárias**</span>

Vamos usar o dataset concursos públicos que já foi preprocessed anteriormente:
- Este dataset tem concursos públicos desde 12/05/2010 a 08/11/2024

In [21]:
concursos_publicos = pd.read_csv("Concursos_Públicos_impic.csv")
concursos_publicos

contract_id                                    contracted_name  \
0           875874  Medicinália Cormédica-Comercialização Produtos...   
1           148916                MRG - ENGENHARIA E CONSTRUÇÃO, S.A.   
2          1076289  PT PRIME - Soluções Empresariais de Telecomuni...   
3           136321                  Euromex - Facility Services, Lda.   
4           600796                  Opção - Sociedade Hoteleira, Lda.   
...            ...                                                ...   
97942     11088884                          Grandatlas Construções SA   
97943     11088891                             Fine Facility Services   
97944     11088904      Multitendas-Comércio e Aluguer de Tendas S.A.   
97945     10813424  JUSTACOLINA- SERVIÇOS DE SILVICUTURA E EXPLORA...   
97946     11043018              Margarida Braz Borges Unipessoal Lda.   

       contracted_nif                                   contestants_name  \
0           500684324  ['Dimor Lusitana,Lda', 'Anastácio Saldanha', '...   
1           500739749  ['Tomás de Oliveira Empreiteiros, S.A', 'OIKOS...   
2           502840757  ['TV CABO LISBOA, S.A.', 'ONITELECOM - Infocom...   
3           502629428  ['Saniambiente Serviços Profissionais de Limpe...   
4           503875716  ['De Almeida Ribeiro Empreendimentos Hoteleiro...   
...               ...                                                ...   
97942       510199712  ['Socodefil Lda', 'Aragão Seia Lda.', 'Grandat...   
97943       509418627  ['Servilimpe Limpezas Técnicas e Mecanizadas S...   
97944       506871541  ['Exemplus Internacional Ldª', 'Jetstand  Mont...   
97945       514746408  ['ECOAMBIENTE - SERVIÇOS E MEIO AMBIENTE S.A.'...   
97946       513279849  ['Margem Mítica-Manutenção e Reabilitação Unip...   

                                         contestants_nif  \
0      ['500730741', '505804441', '507445937', '50341...   
1      ['500285608', '501114998', '500821291', '50073...   
2      ['503039063', '504073206', '502840757', '50260...   
3                ['506665836', '503024155', '502629428']   
4                ['504010298', '504551230', '500545103']   
...                                                  ...   
97942            ['500742219', '509339387', '510199712']   
97943  ['500246505', '516510657', '504458086', '51574...   
97944  ['514999934', '503893684', '516665227', '50687...   
97945  ['502877472', '509482490', '505601800', '50882...   
97946                         ['510800980', '513279849']   

                                 contracting_agency_name  \
0                     Centro Hospitalar de Torres Vedras   
1      VALORLIS Valorização e Tratamento de Resíduos ...   
2                   Santa Casa da Misericórdia de Lisboa   
3                             Município de Torres Vedras   
4                                    Municipio de Oeiras   
...                                                  ...   
97942                        Freguesia de Avenidas Novas   
97943            Ministério da Defesa Nacional - Marinha   
97944                                 Município de Braga   
97945             AdRA - Águas da Região de Aveiro S. A.   
97946                                Município de Sintra   

       contracting_agency_nif       price signing_date execution_district  \
0                   505950413    15450.00   2010-05-12             Lisboa   
1                   503811866  1794202.51   2010-07-30             Leiria   
2                   500745471  9779231.25   2010-11-25             Lisboa   
3                   502173653   103555.17   2010-08-16             Lisboa   
4                   500745943    80655.00   2010-03-25             Lisboa   
...                       ...         ...          ...                ...   
97942               510856861   403966.10   2024-10-30             Lisboa   
97943               600012662     6182.64   2024-05-29            Setubal   
97944               506901173   529612.45   2024-12-11              Braga   
97945

Filtrar este dataset para incluir apenas concursos públicos até 01/01/2021:

In [22]:
# Garantir que signing_date está em formato datetime
concursos_publicos["signing_date"] = pd.to_datetime(
    concursos_publicos["signing_date"],
    errors="coerce"
)

# Filtrar concursos públicos até 01/01/2021 (inclusive)
concursos_publicos = concursos_publicos[
    concursos_publicos["signing_date"] <= "2021-01-01"
].copy()

In [23]:
entidades_adjudicatarias = concursos_publicos[[
    "contracted_nif",
    "contracted_name"]].copy()

# rename columns for clarity
entidades_adjudicatarias.columns = ["NIF", "Nome"]

# drop duplicate rows to get only the unique entities
entidades_adjudicatarias = entidades_adjudicatarias.drop_duplicates()

entidades_adjudicatarias

NIF                                               Nome
0      500684324  Medicinália Cormédica-Comercialização Produtos...
1      500739749                MRG - ENGENHARIA E CONSTRUÇÃO, S.A.
2      502840757  PT PRIME - Soluções Empresariais de Telecomuni...
3      502629428                  Euromex - Facility Services, Lda.
4      503875716                  Opção - Sociedade Hoteleira, Lda.
...          ...                                                ...
51113  514353511         Proteção Mundial - Segurança Privada, Lda.
51173  502266791                  Hikma Farmaceutica (Portugal) Lda
51186  500384045                                 LAB. MEDINFAR, SA.
51234  508622263                  ACCORD HEALTHCARE, Unipessoal Lda
51967  514353511                               Proteção Mundial lda

[19079 rows x 2 columns]

Agora vamos normalizar os nomes das entidades adjudicatarias:

In [24]:
def _norm_name(s: str) -> str:
    s = unidecode(str(s))  #.lower() vamos agora retirar a especificidade de colocar tudo em minúsculas para ver se conseguimos extrair melhor o nome das entidades
    s = re.sub(r"[^\w\s]", " ", s)
    s = re.sub(r"\s+", " ", s).strip()
    s = re.sub(r'(?i)\b(?:\d{7}|[a-z]\s*\d{8,9}|\d{9})\b', ' ', s)
    s = re.sub(r"\s+", " ", s).strip()
    return s

In [25]:
entidades_adjudicatarias_norm = entidades_adjudicatarias.copy()

entidades_adjudicatarias_norm["Nome_normalizado"] = (
    entidades_adjudicatarias_norm["Nome"]
    .apply(_norm_name))

entidades_adjudicatarias_norm

NIF                                               Nome  \
0      500684324  Medicinália Cormédica-Comercialização Produtos...   
1      500739749                MRG - ENGENHARIA E CONSTRUÇÃO, S.A.   
2      502840757  PT PRIME - Soluções Empresariais de Telecomuni...   
3      502629428                  Euromex - Facility Services, Lda.   
4      503875716                  Opção - Sociedade Hoteleira, Lda.   
...          ...                                                ...   
51113  514353511         Proteção Mundial - Segurança Privada, Lda.   
51173  502266791                  Hikma Farmaceutica (Portugal) Lda   
51186  500384045                                 LAB. MEDINFAR, SA.   
51234  508622263                  ACCORD HEALTHCARE, Unipessoal Lda   
51967  514353511                               Proteção Mundial lda   

                                        Nome_normalizado  
0      Medicinalia Cormedica Comercializacao Produtos...  
1                        MRG ENGENHARIA E CONSTRUCAO S A  
2      PT PRIME Solucoes Empresariais de Telecomunica...  
3                          Euromex Facility Services Lda  
4                          Opcao Sociedade Hoteleira Lda  
...                                                  ...  
51113             Protecao Mundial Seguranca Privada Lda  
51173                    Hikma Farmaceutica Portugal Lda  
51186                                    LAB MEDINFAR SA  
51234                   ACCORD HEALTHCARE Unipessoal Lda  
51967                               Protecao Mundial lda  

[19079 rows x 3 columns]

In [26]:
tokens = entidades_adjudicatarias_norm['Nome_normalizado'].fillna("").str.split()
n_tokens = tokens.str.len() 
n_tokens.describe()

count    19079.000000
mean         5.092510
std          2.224195
min          0.000000
25%          3.000000
50%          5.000000
75%          7.000000
max         26.000000
Name: Nome_normalizado, dtype: float64

In [27]:
entidades_adjudicatarias_norm[n_tokens>20]['Nome_normalizado'].values

array(['WATERBETLIS BETONILHAS DO LIS LDA representante do consorcio das empresas ECO COLLIPPO LDA NIPC 509 133 320 WATERBETLIS BETONILHAS DO LIS LDA NIPC 503 621 021',
       'agrupamento de empresas MEO SERVICOS DE COMUNICACOES E MULTIMEDIA S A NIPC PT PRO SERVICOS ADMINISTRATIVOS E DE GESTAO PARTILHADOS S A NIPC',
       'Agrupamento de Empresas Enviman Manutencao de Sistemas Ambientais S A NIPC e GGC Guilherme Goncalves Correia Filhos Lda NIPC 500 360 154',
       'C T G A CENTRO TECNOLOGICO DE GESTAO AMBIENTAL LDA NIPC 503 195 758 E ENVIMAN MANUTENCAO DE SISTEMAS AMBIENTAIS LDA NIPC 510 903 010'],
      dtype=object)

Vamos só remover estes casos problemáticos:

In [28]:
entidades_adjudicatarias_norm = entidades_adjudicatarias_norm.loc[n_tokens <= 20]

In [29]:
entidades_adjudicatarias_norm

NIF                                               Nome  \
0      500684324  Medicinália Cormédica-Comercialização Produtos...   
1      500739749                MRG - ENGENHARIA E CONSTRUÇÃO, S.A.   
2      502840757  PT PRIME - Soluções Empresariais de Telecomuni...   
3      502629428                  Euromex - Facility Services, Lda.   
4      503875716                  Opção - Sociedade Hoteleira, Lda.   
...          ...                                                ...   
51113  514353511         Proteção Mundial - Segurança Privada, Lda.   
51173  502266791                  Hikma Farmaceutica (Portugal) Lda   
51186  500384045                                 LAB. MEDINFAR, SA.   
51234  508622263                  ACCORD HEALTHCARE, Unipessoal Lda   
51967  514353511                               Proteção Mundial lda   

                                        Nome_normalizado  
0      Medicinalia Cormedica Comercializacao Produtos...  
1                        MRG ENGENHARIA E CONSTRUCAO S A  
2      PT PRIME Solucoes Empresariais de Telecomunica...  
3                          Euromex Facility Services Lda  
4                          Opcao Sociedade Hoteleira Lda  
...                                                  ...  
51113             Protecao Mundial Seguranca Privada Lda  
51173                    Hikma Farmaceutica Portugal Lda  
51186                                    LAB MEDINFAR SA  
51234                   ACCORD HEALTHCARE Unipessoal Lda  
51967                               Protecao Mundial lda  

[19075 rows x 3 columns]

Agora vamos eliminar as linhas com `Nome_normalizado` duplicado e manter a ocorrência mais recente, tendo em conta que o nif da entidade pode ter sido alterado ao longo do tempo.

In [30]:
# Mantém a última ocorrência de cada Nome_normalizado
entidades_final_unique = entidades_adjudicatarias_norm.drop_duplicates(subset="Nome_normalizado", keep="last")

# Verifica o resultado
print(entidades_adjudicatarias_norm.shape, " -> ", entidades_final_unique.shape)

(19075, 3)  ->  (14154, 3)


Criar uma lista com todos os nomes das entidades adjudicatárias únicos normalizados:

In [31]:
# Lista de nomes únicos, mantendo a ordem
nomes_entidades_unicos = (entidades_final_unique['Nome_normalizado']
                .fillna('')
                .str.strip()
                .replace('', pd.NA)
                .dropna()
                .tolist())

nomes_entidades_unicos

['Medicinalia Cormedica Comercializacao Produtos Medico Hospitalares Lda',
 'MRG ENGENHARIA E CONSTRUCAO S A',
 'PT PRIME Solucoes Empresariais de Telecomunicacoes SA',
 'Opcao Sociedade Hoteleira Lda',
 'Artur Salgado',
 'Tecnel Electricidade e Telecomunicacoes Lda',
 'Sociedade de Empreitadas FazVia Lda',
 'TOGAMIL Construcoes Lda',
 'JAIME NOGUEIRA FILHOS LDA',
 'Apcol Apoio Logistico e Comercio Internacional Lda',
 'CLINIFAR',
 'Alfagene',
 'Barraqueiro Transportes S A',
 'Sient Sistemas de Engenharia de Transito S A',
 'MAJA Manuel Antonio Jorge Almeida Const S A',
 'Urbitamega Sociedades de Construcoes do Tamega',
 'SONANGIL SA',
 'VIREANAVE LDA',
 'Recolte Recolha Tratamento e Eliminacao de Residuos SA',
 'PROSEGUR Companhia de Seguranca Unipessoal Lda',
 'AGRICORTES COMERCIO DE MAQUINAS E EQUIPAMENTOS',
 'Sociedade de Empreitadas Fazvia Lda',
 'Molnlycke Health Care Comercializacao de Produtos Hospitalares Lda',
 'Ecoedifica Ambiente e Construcoes SA',
 'Irmaos Pinho Resende Ld

## <span style="background-color:#005e81; padding:5px; border-radius:5px;">**3. Extrair corpo da notícia normalizado**</span>

### <span style="background-color:#005e81; padding:5px; border-radius:5px;">**3.1. Web scraping do corpo da notícia e normalização**</span>

In [32]:
# normalização do texto
def _norm_text(s: str) -> str:
    s = unidecode(str(s)) #.lower() vamos agora retirar a especificidade de colocar tudo em minúsculas para ver se conseguimos extrair melhor o nome das entidades
    s = re.sub(r"[^\w\s]", " ", s)
    s = re.sub(r"[^\w\s]", " ", s)          # remove pontuação
    s = re.sub(r"\s+", " ", s).strip(" -").strip()
    return s

# config 
HDRS = {"User-Agent": "Mozilla/5.0 (X11; Linux x86_64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/123.0 Safari/537.36"}
CONNECT_TO, READ_TO = 6, 12
MAX_CHARS = 200_000

def _strip_arquivo_chrome(soup: BeautifulSoup):
    for sel in [
        "#wb-bar",".wb-toolbar","#wm-ipp","#__wb_banner__","header#wb-bar",
        "nav","footer","header","aside",".sidebar","#sidebar",".share",".social",
        ".related",".breadcrumbs",".comments","#comments"
    ]:
        for tag in soup.select(sel):
            tag.decompose()

def _wayback_from_pageview(url: str) -> str | None:
    m_ts   = re.search(r"/page/view/[^/]+/(\d{14})/", url)
    m_rest = re.search(r"/page/view/[^/]+/\d{14}/(.+)$", url)
    if m_ts and m_rest:
        ts = m_ts.group(1); original = unquote(m_rest.group(1))
        return f"https://arquivo.pt/wayback/{ts}/{original}"
    return None

def make_session():
    s = requests.Session()
    retry = Retry(total=3, connect=3, read=3, backoff_factor=0.5,
                  status_forcelist=[429,500,502,503,504], raise_on_status=False)
    adapter = HTTPAdapter(max_retries=retry, pool_connections=20, pool_maxsize=20)
    s.mount("http://", adapter); s.mount("https://", adapter)
    return s

def _clean_get_text(tag) -> str:
    if not tag: return ""
    txt = tag.get_text(" ", strip=True)
    return re.sub(r"\s+", " ", txt)

def _extract_main_text_from_html_bytes(html_bytes: bytes) -> str:
    # usar BYTES evita moji-bake; lxml/BS detetam a encoding do <meta> ou HTTP
    soup = BeautifulSoup(html_bytes, "lxml")

    for t in soup(["script","style","noscript","iframe"]): t.decompose()
    _strip_arquivo_chrome(soup)

    # 1) tentativas comuns de corpo
    CAND_SEL = [
        "article","main","[role=main]",
        ".entry-content",".post-content",".article-body",".story-body",
        "#content","#main","#article",".conteudo",".texto",".text"
    ]
    best_txt, best_len = "", 0
    for sel in CAND_SEL:
        for node in soup.select(sel):
            txt = _clean_get_text(node)
            if len(txt) > best_len:
                best_txt, best_len = txt, len(txt)
    if best_len >= 200:
        return best_txt[:MAX_CHARS]

    # 2) fallback: maior bloco com <p>
    candidates = []
    for node in soup.find_all(["article","main","section","div"]):
        if len(node.find_all("p")) >= 2:
            txt = _clean_get_text(node)
            candidates.append((len(txt), txt))
    if candidates:
        candidates.sort(reverse=True)
        return candidates[0][1][:MAX_CHARS]

    # 3) último recurso: body limpo
    body = soup.body or soup
    return _clean_get_text(body)[:MAX_CHARS]

def fetch_main_text(url: str, session: requests.Session | None = None) -> str:
    sess = session or requests
    try:
        r = sess.get(url, headers=HDRS, timeout=(CONNECT_TO, READ_TO), allow_redirects=True)
        r.raise_for_status()
    except Exception:
        return ""
    # trabalhar sempre com BYTES
    soup = BeautifulSoup(r.content, "lxml")
    iframe = soup.find("iframe")
    replay = urljoin("https://arquivo.pt", iframe["src"]) if iframe and iframe.get("src") else _wayback_from_pageview(url)
    if replay:
        try:
            rr = sess.get(replay, headers=HDRS, timeout=(CONNECT_TO, READ_TO), allow_redirects=True)
            rr.raise_for_status()
            return _extract_main_text_from_html_bytes(rr.content)
        except Exception:
            pass
    return _extract_main_text_from_html_bytes(r.content)

def add_corpo_da_noticia(df: pd.DataFrame, link_col="link",
                         out_col_raw="corpo_da_noticia",
                         out_col_norm="corpo_norm",
                         max_workers=8) -> pd.DataFrame:
    urls = df[link_col].fillna("").astype(str).tolist()
    sess = make_session()
    textos = [""] * len(urls)
    with ThreadPoolExecutor(max_workers=max_workers) as ex:
        futs = {ex.submit(fetch_main_text, u, sess): i for i, u in enumerate(urls)}
        for fut in as_completed(futs):
            i = futs[fut]
            try:
                textos[i] = fut.result()
            except Exception:
                textos[i] = ""
    out = df.copy()
    out[out_col_raw] = textos                 # texto correto (acentos OK)
    out[out_col_norm] = out[out_col_raw].map(_norm_text)  # normalizado como os nomes
    return out

In [33]:
# NAO CORRER ISTO OUTRA VEZ! ESTÁ GUARDADO NO CSV

df_links_notícia_popular_journals = add_corpo_da_noticia(
    links_popular_journals,  # usar o dataframe da api so com o link e o jornal
    link_col="link",
    out_col_raw="corpo_da_noticia",
    out_col_norm="corpo_norm",   # <- igual à normalização dos nomes
    max_workers=8
)

df_links_notícia_popular_journals

df_links_notícia_popular_journals.to_csv("links_notícia_popular_journals.csv", index=False)

C:\Users\beatr\AppData\Local\Temp\ipykernel_24584\894933929.py:46: XMLParsedAsHTMLWarning: It looks like you're using an HTML parser to parse an XML document.

Assuming this really is an XML document, what you're doing might work, but you should know that using an XML parser will be more reliable. To parse this document as XML, make sure you have the Python package 'lxml' installed, and pass the keyword argument `features="xml"` into the BeautifulSoup constructor.

If you want or need to use an HTML parser on this document, you can make this warning go away by filtering it. To do that, run this code before calling the BeautifulSoup constructor:

    from bs4 import XMLParsedAsHTMLWarning
    import warnings

    warnings.filterwarnings("ignore", category=XMLParsedAsHTMLWarning)

  soup = BeautifulSoup(html_bytes, "lxml")


In [34]:
df_links_notícia_popular_journals

link        _captured_at  \
0    https://arquivo.pt/wayback/20210101035654/http... 2021-01-01 03:56:54   
1    https://arquivo.pt/wayback/20210101035650/http... 2021-01-01 03:56:50   
2    https://arquivo.pt/wayback/20210101000938/http... 2021-01-01 00:09:38   
3    https://arquivo.pt/wayback/20201228224031/http... 2020-12-28 22:40:31   
4    https://arquivo.pt/wayback/20201226192545/http... 2020-12-26 19:25:45   
..                                                 ...                 ...   
836  https://arquivo.pt/wayback/20100624063145/http... 2010-06-24 06:31:45   
837  https://arquivo.pt/wayback/20100612030446/http... 2010-06-12 03:04:46   
838  https://arquivo.pt/wayback/20100606164020/http... 2010-06-06 16:40:20   
839  https://arquivo.pt/wayback/20100606163914/http... 2010-06-06 16:39:14   
840  https://arquivo.pt/wayback/20100602145911/http... 2010-06-02 14:59:11   

                 jornal                                   corpo_da_noticia  \
0                   TSF  Por Pedro Pinheiro (TSF) e João Pedro Henrique...   
1                   TSF  Tópicos chave Costa e Marcelo responsáveis em ...   
2            Observador  CORONAVÍRUS O que tem de saber Situação em Por...   
3    Diário de Notícias                                           Ver mais   
4      Jornal Económico  Objetivo Opinião A concorrência João Marcelino...   
..                  ...                                                ...   
836             Público  Tecnologia Associação de Empresas de Software ...   
837                 SOL  Entrar | Criar Registo Criar Blogue Criar Álbu...   
838  Jornal de Negócios  Publicado 19 Setembro 2008 00:01 Empresas Empr...   
839  Jornal de Negócios  Página Inicial | Actualizar | Favoritos | A su...   
840            Expresso  02/06/2010 actualizado às 15:55 Blogues RSS Ed...   

                                            corpo_norm  
0    Por Pedro Pinheiro TSF e Joao Pedro Henriques ...  
1    Topicos chave Costa e Marcelo responsaveis em ...  
2    CORONAVIRUS O que tem de saber Situacao em Por...  
3                                             Ver mais  
4    Objetivo Opiniao A concorrencia Joao Marcelino...  
..                                                 ...  
836  Tecnologia Associacao de Empresas de Software ...  
837  Entrar Criar Registo Criar Blogue Criar Album ...  
838  Publicado 19 Setembro 2008 00 01 Empresas Empr...  
839  Pagina Inicial Actualizar Favoritos A sua Home...  
840  02 06 2010 actualizado as 15 55 Blogues RSS Ed...  

[841 rows x 5 columns]

In [35]:
df_links_notícia_popular_journals['corpo_da_noticia'][4]

'Objetivo Opinião A concorrência João Marcelino 24 Dezembro 2020, 00:17 Os 304 milhões de euros de multas que a Autoridade da Concorrência aplicou a seis cadeias de supermercados e dois fornecedores de bebidas são um novo sinal de esperança para os consumidores. 1. O conceito de concorrência é essencial para a salvaguarda dos consumidores, que somos todos. Em Portugal, país pequeno, às vezes insuportavelmente pequeno e asfixiante, até há uns quatro anos pouco se tinha dado pela sua existência, o que é estranho, pois que desde 2003 existe um organismo regulador, a chamada Autoridade da Concorrência (AdC). É a esta entidade que cabe assegurar o respeito pelo funcionamento da economia de mercado e da livre concorrência. Como vemos, não tem sido fácil. Todos os dias nos chegam rumores de conluio em concursos públicos, seja na administração central ou local, na aquisição de produtos ou serviços. Acontece em autarquias, escolas, hospitais, tribunais, outras estruturas. Os concorrentes fazem 

### <span style="background-color:#005e81; padding:5px; border-radius:5px;">**3.2. Processamento e Filtragem**</span>

Filtrar as notícias com base nestes 2 critérios:

- Filtrar notícias com corpo da notícia duplicado e manter primeira ocorrência.
- Excluir todas as notícias que não contenham pelo menos uma das seguintes expressões: `cartel/cartéis`, `concurso publico`, `concursos publicos`, `irregularidade(s)`, `Autoridade da Concorrência`, `Tribunal de Contas`, `conluio(s)` no seu corpo da notícia. 

In [36]:
# expressões desejadas (sem acentos; vamos comparar numa versão sem acentos do corpo)
_PHRASES = [
    "cartel", "carteis",                 
    "concurso publico",
    "concursos publicos",
    "irregularidade", "irregularidades",
    "autoridade da concorrencia",
    "tribunal de contas",
    "conluio", "conluios"]

# compilar regex OR com bordas de palavra frouxas (permitir acentos removidos e espaços)
_PATTERN = re.compile(r"(?:%s)" % "|".join(map(re.escape, _PHRASES)), flags=re.I)

def preprocess_noticias(
    df: pd.DataFrame,
    cols: dict | None = None
) -> tuple[pd.DataFrame, pd.DataFrame]:
    """
    1) Dedupe por corpo_da_noticia (mantém 1ª ocorrência)
    2) Manter apenas linhas cujo corpo_da_noticia contém >=1 das expressões alvo
       (matching case-insensitive e accent-insensitive)
    """
    c_body = (cols or {}).get("body", "corpo_da_noticia")

    report_rows = []
    cur = df.copy()
    n0 = len(cur)
    report_rows.append({"passo": "0_inicial", "antes": n0, "depois": n0, "removidas": 0})

    # 1) duplicados pelo corpo (primeira ocorrência)
    if c_body in cur.columns:
        cur1 = cur.drop_duplicates(subset=c_body).reset_index(drop=True)
    else:
        cur1 = cur.copy()
    n1 = len(cur1)
    report_rows.append({"passo": "1_dup_corpo", "antes": n0, "depois": n1, "removidas": n0 - n1})

    # 2) filtrar por expressões no próprio corpo_da_noticia (accent-insensitive)
    if c_body in cur1.columns:
        body_noacc = cur1[c_body].astype(str).map(lambda s: unidecode(s.lower()))
        mask = body_noacc.str.contains(_PATTERN, na=False)
        cur_final = cur1[mask].reset_index(drop=True)
    else:
        cur_final = cur1
    n2 = len(cur_final)
    report_rows.append({"passo": "2_filtrar_expressoes", "antes": n1, "depois": n2, "removidas": n1 - n2})

    report = pd.DataFrame(report_rows)
    return cur_final, report

In [37]:
df_popular_journals_final, rpt = preprocess_noticias(df_links_notícia_popular_journals)
print(rpt)
df_popular_journals_final

                  passo  antes  depois  removidas
0             0_inicial    841     841          0
1           1_dup_corpo    841     785         56
2  2_filtrar_expressoes    785     603        182


link        _captured_at  \
0    https://arquivo.pt/wayback/20210101035654/http... 2021-01-01 03:56:54   
1    https://arquivo.pt/wayback/20210101035650/http... 2021-01-01 03:56:50   
2    https://arquivo.pt/wayback/20210101000938/http... 2021-01-01 00:09:38   
3    https://arquivo.pt/wayback/20201226192545/http... 2020-12-26 19:25:45   
4    https://arquivo.pt/wayback/20201225203136/http... 2020-12-25 20:31:36   
..                                                 ...                 ...   
598  https://arquivo.pt/wayback/20100624063145/http... 2010-06-24 06:31:45   
599  https://arquivo.pt/wayback/20100612030446/http... 2010-06-12 03:04:46   
600  https://arquivo.pt/wayback/20100606164020/http... 2010-06-06 16:40:20   
601  https://arquivo.pt/wayback/20100606163914/http... 2010-06-06 16:39:14   
602  https://arquivo.pt/wayback/20100602145911/http... 2010-06-02 14:59:11   

                 jornal                                   corpo_da_noticia  \
0                   TSF  Por Pedro Pinheiro (TSF) e João Pedro Henrique...   
1                   TSF  Tópicos chave Costa e Marcelo responsáveis em ...   
2            Observador  CORONAVÍRUS O que tem de saber Situação em Por...   
3      Jornal Económico  Objetivo Opinião A concorrência João Marcelino...   
4                   ECO  O grupo parlamentar do PS vai apresentar no in...   
..                  ...                                                ...   
598             Público  Tecnologia Associação de Empresas de Software ...   
599                 SOL  Entrar | Criar Registo Criar Blogue Criar Álbu...   
600  Jornal de Negócios  Publicado 19 Setembro 2008 00:01 Empresas Empr...   
601  Jornal de Negócios  Página Inicial | Actualizar | Favoritos | A su...   
602            Expresso  02/06/2010 actualizado às 15:55 Blogues RSS Ed...   

                                            corpo_norm  
0    Por Pedro Pinheiro TSF e Joao Pedro Henriques ...  
1    Topicos chave Costa e Marcelo responsaveis em ...  
2    CORONAVIRUS O que tem de saber Situacao em Por...  
3    Objetivo Opiniao A concorrencia Joao Marcelino...  
4    O grupo parlamentar do PS vai apresentar no in...  
..                                                 ...  
598  Tecnologia Associacao de Empresas de Software ...  
599  Entrar Criar Registo Criar Blogue Criar Album ...  
600  Publicado 19 Setembro 2008 00 01 Empresas Empr...  
601  Pagina Inicial Actualizar Favoritos A sua Home...  
602  02 06 2010 actualizado as 15 55 Blogues RSS Ed...  

[603 rows x 5 columns]

## <span style="background-color:#005e81; padding:5px; border-radius:5px;">**4. Identificação das entidades no corpo da notícia**</span>

### <span style="background-color:#005e81; padding:5px; border-radius:5px;">**4.1. NER (Named Entity Recognition) - ORG**</span>

In [38]:
df_popular_journals_final['corpo_da_noticia']

0      Por Pedro Pinheiro (TSF) e João Pedro Henrique...
1      Tópicos chave Costa e Marcelo responsáveis em ...
2      CORONAVÍRUS O que tem de saber Situação em Por...
3      Objetivo Opinião A concorrência João Marcelino...
4      O grupo parlamentar do PS vai apresentar no in...
                             ...                        
598    Tecnologia Associação de Empresas de Software ...
599    Entrar | Criar Registo Criar Blogue Criar Álbu...
600    Publicado 19 Setembro 2008 00:01 Empresas Empr...
601    Página Inicial | Actualizar | Favoritos | A su...
602    02/06/2010 actualizado às 15:55 Blogues RSS Ed...
Name: corpo_da_noticia, Length: 603, dtype: object

In [39]:
nlp = spacy.load("pt_core_news_lg")

In [40]:
def extract_orgs(text: str):
    if not isinstance(text, str) or not text.strip():
        return []
    doc = nlp(text)
    orgs = [ent.text.strip() for ent in doc.ents if ent.label_ == "ORG"]
    # deduplicar mantendo ordem
    seen = set()
    out = []
    for o in orgs:
        o2 = " ".join(o.split())
        if o2 and o2 not in seen:
            seen.add(o2)
            out.append(o2)
    return out


In [41]:
df_popular_journals_final["orgs"] = df_popular_journals_final["corpo_da_noticia"].apply(extract_orgs)

In [42]:
df_popular_journals_final

link        _captured_at  \
0    https://arquivo.pt/wayback/20210101035654/http... 2021-01-01 03:56:54   
1    https://arquivo.pt/wayback/20210101035650/http... 2021-01-01 03:56:50   
2    https://arquivo.pt/wayback/20210101000938/http... 2021-01-01 00:09:38   
3    https://arquivo.pt/wayback/20201226192545/http... 2020-12-26 19:25:45   
4    https://arquivo.pt/wayback/20201225203136/http... 2020-12-25 20:31:36   
..                                                 ...                 ...   
598  https://arquivo.pt/wayback/20100624063145/http... 2010-06-24 06:31:45   
599  https://arquivo.pt/wayback/20100612030446/http... 2010-06-12 03:04:46   
600  https://arquivo.pt/wayback/20100606164020/http... 2010-06-06 16:40:20   
601  https://arquivo.pt/wayback/20100606163914/http... 2010-06-06 16:39:14   
602  https://arquivo.pt/wayback/20100602145911/http... 2010-06-02 14:59:11   

                 jornal                                   corpo_da_noticia  \
0                   TSF  Por Pedro Pinheiro (TSF) e João Pedro Henrique...   
1                   TSF  Tópicos chave Costa e Marcelo responsáveis em ...   
2            Observador  CORONAVÍRUS O que tem de saber Situação em Por...   
3      Jornal Económico  Objetivo Opinião A concorrência João Marcelino...   
4                   ECO  O grupo parlamentar do PS vai apresentar no in...   
..                  ...                                                ...   
598             Público  Tecnologia Associação de Empresas de Software ...   
599                 SOL  Entrar | Criar Registo Criar Blogue Criar Álbu...   
600  Jornal de Negócios  Publicado 19 Setembro 2008 00:01 Empresas Empr...   
601  Jornal de Negócios  Página Inicial | Actualizar | Favoritos | A su...   
602            Expresso  02/06/2010 actualizado às 15:55 Blogues RSS Ed...   

                                            corpo_norm  \
0    Por Pedro Pinheiro TSF e Joao Pedro Henriques ...   
1    Topicos chave Costa e Marcelo responsaveis em ...   
2    CORONAVIRUS O que tem de saber Situacao em Por...   
3    Objetivo Opiniao A concorrencia Joao Marcelino...   
4    O grupo parlamentar do PS vai apresentar no in...   
..                                                 ...   
598  Tecnologia Associacao de Empresas de Software ...   
599  Entrar Criar Registo Criar Blogue Criar Album ...   
600  Publicado 19 Setembro 2008 00 01 Empresas Empr...   
601  Pagina Inicial Actualizar Favoritos A sua Home...   
602  02 06 2010 actualizado as 15 55 Blogues RSS Ed...   

                                                  orgs  
0    [TSF, DN, Direito, PS, PCP, Bloco de Esquerda,...  
1    [Tribunal de Contas, CCDR's, Direito, PS, PCP,...  
2    [Galp, Plano Nacional de Investimentos 2030, A...  
3    [Autoridade da Concorrência, AdC, Justiça, Auc...  
4    [PS, Assembleia da República, PSD, ECO, Parlam...  
..                                                 ...  
598  [Associação de Empresas de Software Open Sourc...  
599  [UnI, Uni, PS, UnI 18 ABR 07 UnI, União Europe...  
600  [Empresas Empresas, Autoridade da Concorrência...  
601  [Estatísticas de Bolsa, Autoridade da Concorrê...  
602  [PT, SIC, Globo, Presidente Telefónica, Escola...  

[603 rows x 6 columns]

### <span style="background-color:#005e81; padding:5px; border-radius:5px;">**4.2. Matching extracted entities with adjudicated firms**</span>

Vamos usar a mesma função `_norm_name` usada para normalizar os nomes das entidades adjudicatárias, para normalizar as entidades extraídas pelo NER.

In [ ]:
# normalizar ORGs 
def normalize_orgs_list(orgs_list):
    if not isinstance(orgs_list, list) or len(orgs_list) == 0:
        return []
    out = []
    seen = set()
    for o in orgs_list:
        o_norm = _norm_name(o)
        if not isinstance(o_norm, str) or not o_norm.strip():
            continue
        if o_norm not in seen:
            seen.add(o_norm)
            out.append(o_norm)
    return out

df_popular_journals_final["orgs_norm"] = df_popular_journals_final["orgs"].apply(normalize_orgs_list)

In [58]:
def adaptive_cutoff(n_orgs: int) -> int:
    """
    Cutoff adaptativo para fuzzy matching.
    Quanto menos ORGs no texto, mais exigente o threshold.
    """
    if n_orgs <= 1:
        return 96
    if n_orgs == 2:
        return 94
    if n_orgs == 3:
        return 92
    if n_orgs <= 5:
        return 90
    if n_orgs <= 8:
        return 88
    return 86

In [ ]:
def match_one_org_norm(
    org_norm: str,
    nomes_entidades_unicos: list,
    score_cutoff: int = 90
):
    """
    org_norm: nome da organização já normalizado
    nomes_entidades_unicos: lista de adjudicatárias normalizadas
    retorna (best_match, score) ou (None, score)
    """
    if not isinstance(org_norm, str) or not org_norm.strip():
        return None, 0

    best = process.extractOne(
        org_norm,
        nomes_entidades_unicos,
        scorer=fuzz.token_set_ratio
    )

    if best is None:
        return None, 0

    match_name, score, _ = best
    if score >= score_cutoff:
        return match_name, score

    return None, score

In [ ]:
def match_orgs_to_adjudicatarias(
    orgs_norm_list,
    nomes_entidades_unicos,
    score_cutoff: int = 90
):
    """
    orgs_norm_list: lista de ORGs normalizadas
    retorna:
      - matches: lista única de adjudicatárias matched
      - details: lista de dicts com org, match e score
    """
    if not isinstance(orgs_norm_list, list) or len(orgs_norm_list) == 0:
        return [], []

    matches = []
    details = []
    seen_matches = set()

    for org_n in orgs_norm_list:
        m, sc = match_one_org_norm(
            org_n,
            nomes_entidades_unicos,
            score_cutoff=score_cutoff
        )

        if m is not None:
            details.append({
                "org_norm": org_n,
                "match": m,
                "score": sc
            })

            if m not in seen_matches:
                seen_matches.add(m)
                matches.append(m)

    return matches, details

In [56]:
SCORE_CUTOFF = 95

tmp = df_popular_journals_final["orgs_norm"].apply(
    lambda xs: match_orgs_to_adjudicatarias(
        xs,
        nomes_entidades_unicos,
        score_cutoff=SCORE_CUTOFF))

df_popular_journals_final["matches_adj"] = tmp.apply(lambda t: t[0])
df_popular_journals_final["matches_detail"] = tmp.apply(lambda t: t[1])


In [57]:
df_popular_journals_final

link        _captured_at  \
0    https://arquivo.pt/wayback/20210101035654/http... 2021-01-01 03:56:54   
1    https://arquivo.pt/wayback/20210101035650/http... 2021-01-01 03:56:50   
2    https://arquivo.pt/wayback/20210101000938/http... 2021-01-01 00:09:38   
3    https://arquivo.pt/wayback/20201226192545/http... 2020-12-26 19:25:45   
4    https://arquivo.pt/wayback/20201225203136/http... 2020-12-25 20:31:36   
..                                                 ...                 ...   
598  https://arquivo.pt/wayback/20100624063145/http... 2010-06-24 06:31:45   
599  https://arquivo.pt/wayback/20100612030446/http... 2010-06-12 03:04:46   
600  https://arquivo.pt/wayback/20100606164020/http... 2010-06-06 16:40:20   
601  https://arquivo.pt/wayback/20100606163914/http... 2010-06-06 16:39:14   
602  https://arquivo.pt/wayback/20100602145911/http... 2010-06-02 14:59:11   

                 jornal                                   corpo_da_noticia  \
0                   TSF  Por Pedro Pinheiro (TSF) e João Pedro Henrique...   
1                   TSF  Tópicos chave Costa e Marcelo responsáveis em ...   
2            Observador  CORONAVÍRUS O que tem de saber Situação em Por...   
3      Jornal Económico  Objetivo Opinião A concorrência João Marcelino...   
4                   ECO  O grupo parlamentar do PS vai apresentar no in...   
..                  ...                                                ...   
598             Público  Tecnologia Associação de Empresas de Software ...   
599                 SOL  Entrar | Criar Registo Criar Blogue Criar Álbu...   
600  Jornal de Negócios  Publicado 19 Setembro 2008 00:01 Empresas Empr...   
601  Jornal de Negócios  Página Inicial | Actualizar | Favoritos | A su...   
602            Expresso  02/06/2010 actualizado às 15:55 Blogues RSS Ed...   

                                            corpo_norm  \
0    Por Pedro Pinheiro TSF e Joao Pedro Henriques ...   
1    Topicos chave Costa e Marcelo responsaveis em ...   
2    CORONAVIRUS O que tem de saber Situacao em Por...   
3    Objetivo Opiniao A concorrencia Joao Marcelino...   
4    O grupo parlamentar do PS vai apresentar no in...   
..                                                 ...   
598  Tecnologia Associacao de Empresas de Software ...   
599  Entrar Criar Registo Criar Blogue Criar Album ...   
600  Publicado 19 Setembro 2008 00 01 Empresas Empr...   
601  Pagina Inicial Actualizar Favoritos A sua Home...   
602  02 06 2010 actualizado as 15 55 Blogues RSS Ed...   

                                                  orgs  \
0    [TSF, DN, Direito, PS, PCP, Bloco de Esquerda,...   
1    [Tribunal de Contas, CCDR's, Direito, PS, PCP,...   
2    [Galp, Plano Nacional de Investimentos 2030, A...   
3    [Autoridade da Concorrência, AdC, Justiça, Auc...   
4    [PS, Assembleia da República, PSD, ECO, Parlam...   
..                                                 ...   
598  [Associação de Empresas de Software Open Sourc...   
599  [UnI, Uni, PS, UnI 18 ABR 07 UnI, União Europe...   
600  [Empresas Empresas, Autoridade da Concorrência...   
601  [Estatísticas de Bolsa, Autoridade da Concorrê...   
602  [PT, SIC, Globo, Presidente Telefónica, Escola...   

                                             orgs_norm  \
0    [TSF, DN, Direito, PS, PCP, Bloco de Esquerda,...   
1    [Tribunal de Contas, CCDR s, Direito, PS, PCP,...   
2    [Galp, Plano Nacional de Investimentos 2030, A...   
3    [Autoridade da Concorrencia, AdC, Justica, Auc...   
4    [PS, Assembleia da Republica, PSD, ECO, Parlam...   
..                                                 ...   
598  [Associacao de Empresas de Software Open Sourc...   
599  [UnI, Uni, PS, UnI 18 ABR 07 UnI, Uniao Europe...   
600  [Empresas Empresas, Autoridade da Concorrencia...   
601  [Estatisticas de Bolsa, Autoridade da Concorre...   
602  [PT, SIC, Globo, Presidente Telefonica, Escola...   

                                           matches_adj  \
0    [Instituto Ciencias Ju